# Project 1 - Functions tests

In [1]:
from preprocessing_functions import *
%matplotlib inline 
import numpy as np   # generic stuff
import matplotlib.pyplot as plt

#### REMOVE THIS LINE BEFORE SUBMISSION
import pandas as pd
#######################################################################

from lib.helpers import * #the helper provided for the project
# choose which implementations you would like
from lib.implementations import *

%load_ext autoreload
%autoreload 2
%reload_ext autoreload

In [2]:
DATA_FOLDER = 'data/' 

y_train, tx_train, ids_train = load_csv_data(DATA_FOLDER+'train.csv',sub_sample=False)
size_train = int(3*len(y_train)/4)
y_test = y_train[:size_train]
tx_test = tx_train[:size_train,:]
ids_test = ids_train[:size_train]

y_train = y_train[size_train:]
tx_train = tx_train[size_train:,:]
ids_train = ids_train[size_train:]

#y_test, tx_test, ids_test = load_csv_data(DATA_FOLDER+'test.csv',sub_sample=False)

In [3]:
def build_k_indices(y, k_fold, seed):
    """Build k indices for k-fold."""
    num_row = y.shape[0]
    interval = int(num_row / k_fold)
    np.random.seed(seed)
    indices = np.random.permutation(num_row)
    k_indices = [indices[k * interval: (k + 1) * interval]
                 for k in range(k_fold)]
    return np.array(k_indices)

In [4]:
def cross_validation_one_fold_LS(y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, \
                                 degrees, len_kept_data, stdize=False):
    
    accuracies_train_by_deg = np.zeros(len(degrees))
    accuracies_test_by_deg = np.zeros(len(degrees))
    
    # For each degree, compute the least squares weights, the predictions and the accuracies
    previous_deg = 1
    for deg_id, deg in enumerate(degrees):
        print('++ Degree', deg, '++')
        
        # Add powers of the chosen columns
        len_data = tx_cross_val_train.shape[1]
        tx_cross_val_train = add_powers(tx_cross_val_train, range(previous_deg+1, deg+1), range(len_kept_data))
        tx_cross_val_test = add_powers(tx_cross_val_test, range(previous_deg+1, deg+1), range(len_kept_data))
        if stdize: 
            tx_cross_val_train[:,len_data:] = standardize(tx_cross_val_train[:,len_data:])[0]
            tx_cross_val_test[:,len_data:] = standardize(tx_cross_val_test[:,len_data:])[0]
    
        # Compute the best weights on the training set
        weights, loss = least_squares(y_cross_val_train, tx_cross_val_train, 'mse') 

        # Compute the predictions
        y_predicted_cross_val_train = predict_labels(weights, tx_cross_val_train)
        y_predicted_cross_val_test = predict_labels(weights, tx_cross_val_test)

        # Compute the accuracies for each degree
        accuracies_train_by_deg[deg_id] = \
            np.sum(y_predicted_cross_val_train == y_cross_val_train)/len(y_cross_val_train)
        accuracies_test_by_deg[deg_id] = \
            np.sum(y_predicted_cross_val_test == y_cross_val_test)/len(y_cross_val_test)
        
        # Update the previous degree to the actual degree
        previous_deg = deg
        
    return accuracies_train_by_deg, accuracies_test_by_deg

In [23]:
def cross_validation_least_squares(y_single_jet_train, tx_single_jet_train, degrees, k_fold, seed):
    
    # Get the indices so that we get the k'th subgroup in test, others in train, for each k
    k_indices = build_k_indices(y_single_jet_train, k_fold, seed)
    
    # Initialize matrix of computed accuracies for each degree and each fold
    accuracies_train_by_fold = np.zeros([len(degrees), k_fold])
    accuracies_test_by_fold = np.zeros([len(degrees), k_fold])
    
    # Preprocess training dataset
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'none')
    
    for k in range(k_fold):
        print('--- Fold', k, '---')
        # Create the testing set for this fold number
        k_index = k_indices[k] # Indices of the testing set for fold k
        y_cross_val_test = y_single_jet_train[k_index]
        tx_cross_val_test = tx_single_jet_train_preprocessed[k_index,:]
        
        # Create the training set for this fold number
        mask = np.ones(len(y_single_jet_train), dtype=bool) # set all elements to True
        mask[k_index] = False # set test elements to False
        y_cross_val_train = y_single_jet_train[mask] # select only True elements (ie train elements)
        tx_cross_val_train = tx_single_jet_train_preprocessed[mask,:]
        
        # Compute the accuracies for each degree
        accuracies_train_by_fold[:,k], accuracies_test_by_fold[:,k] = cross_validation_one_fold_LS\
            (y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, degrees, len_kept_data, \
             False)
    
    # Compute the mean accuracies over the folds, for each degree
    mean_accuracies_train_by_deg = np.mean(accuracies_train_by_fold, axis=1)
    mean_accuracies_test_by_deg = np.mean(accuracies_test_by_fold, axis=1)
    
    # Get the index of the best accuracy in the testing set
    max_id_deg_test = np.unravel_index(mean_accuracies_test_by_deg.argmax(), mean_accuracies_test_by_deg.shape)
    
    # Find the optimal degree and the corresponding accuracies in the training and testing sets
    best_deg = degrees[max_id_deg_test[0]]
    best_accuracy_test = mean_accuracies_test_by_deg[max_id_deg_test[0]]
    corresponding_accuracy_train = mean_accuracies_train_by_deg[max_id_deg_test[0]]
    
    print('Best accuracy test =', best_accuracy_test, 'with degree =', best_deg)
    print('Corresponding accuracy train =', corresponding_accuracy_train)
    
    return best_deg, best_accuracy_test, corresponding_accuracy_train

In [24]:
degrees = range(6,11)
k_fold = 5
seed = 1

In [25]:
mask_jets_train = split_jets_mask(tx_train)
mask_jets_test = split_jets_mask(tx_test)
len_mask = len(mask_jets_train)

y_predicted_train = np.zeros(len(y_train))
y_predicted_test = np.zeros(tx_test.shape[0])
best_degrees = np.zeros(len_mask)

In [ ]:
for jet_id in range(len_mask):
    print('***** Jet ', jet_id, '*****')
    # SEPARATE THE WHOLE DATA SET TO GET ONLY THE PART THAT HAVE THE RIGHT NUMBER OF JETS
    tx_single_jet_train = tx_train[mask_jets_train[jet_id]]
    tx_single_jet_test = tx_test[mask_jets_test[jet_id]]
    y_single_jet_train = y_train[mask_jets_train[jet_id]]
    
    # CALL CROSS VALIDATION FOR A SINGLE JET ON TRAIN PART, FIND BEST DEG, BEST ACCURACY ON TESTING CROSS VAL
    best_deg, best_accuracy, corresponding_accuracy_train = cross_validation_least_squares(y_single_jet_train, \
                                                                                           tx_single_jet_train, \
                                                                                           degrees, k_fold, seed)
    
    # KEEP IN MEMORY THE BEST DEGREE FOR THIS JET
    best_degrees[jet_id] = best_deg
    
    # PREPROCESS FULL TRAINING AND TESTING DATA
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'none')
    tx_single_jet_test_preprocessed = preprocess_data(tx_single_jet_test, unique_cols, 'none')[0]
    
    # ADD POWERS TO THE CHOSEN COLUMNS
    tx_single_jet_train_preprocessed = add_powers(tx_single_jet_train_preprocessed, range(2,best_deg+1), \
                                                  range(len_kept_data))
    tx_single_jet_test_preprocessed = add_powers(tx_single_jet_test_preprocessed, range(2,best_deg+1), \
                                                 range(len_kept_data))
    
    # COMPUTE THE BEST WEIGHTS AND FULL ACCURACY ON TRAINING FULL SET - ONE JET
    weights, loss = least_squares(y_single_jet_train, tx_single_jet_train_preprocessed, 'mse')
    
    # COMPUTE THE PREDICTIONS ON THE FULL TESTING SET - SINGLE JET
    y_predicted_single_jet_train = predict_labels(weights, tx_single_jet_train_preprocessed)
    y_predicted_single_jet_test = predict_labels(weights, tx_single_jet_test_preprocessed)
    
    # ADD THE PREDICTIONS TO y_predicted_test AND y_predicted_train
    y_predicted_train[mask_jets_train[jet_id]] = y_predicted_single_jet_train
    y_predicted_test[mask_jets_test[jet_id]] = y_predicted_single_jet_test
    
    # COMPUTE THE ACCURACY train ON JET
    accuracy_train_single_jet = np.sum(y_predicted_single_jet_train == y_single_jet_train)/len(y_single_jet_train)
    
    # PRINT ACCURACY train ON JET
    print('Accuracy full train on jet', jet_id, '=', accuracy_train_single_jet)

***** Jet  0 *****
--- Fold 0 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++
--- Fold 1 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++
--- Fold 2 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++
--- Fold 3 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++
--- Fold 4 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++
Best accuracy test = 0.843811434303 with degree = 7
Corresponding accuracy train = 0.847024018453
Accuracy full train on jet 0 = 0.846076700899
***** Jet  1 *****
--- Fold 0 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++
--- Fold 1 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++
--- Fold 2 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++
--- Fold 3 ---
++ Degree 6 ++
++ Degree 7 ++
++ Degree 8 ++
++ Degree 9 ++
++ Degree 10 ++

In [14]:
# CREATE CSV SUBMISSION
#create_csv_submission(ids_test, y_predicted_test, 'output/trial.csv')

# COMPUTE ACCURACY ON FULL train
total_accuracy_train = np.sum(y_predicted_train == y_train)/len(y_train)*100
print('Total accuracy train =', total_accuracy_train, 'with degrees =', best_degrees)

Total accuracy train = 97.84 with degrees = [ 6.  7.  6.  6.]


In [21]:
total_accuracy_test = np.sum(y_predicted_test == y_test)/len(y_test)*100
print('Total accuracy test =', total_accuracy_test, 'with degrees =', best_degrees)

Total accuracy test = 65.2533333333 with degrees = [ 6.  7.  6.  6.]


## Gradient descent 

In [22]:
def cross_validation_one_fold_GD(y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, \
                                 degrees, gammas, len_kept_data, max_iters, stdize=False):
    
    accuracies_train_by_deg = np.zeros([len(degrees), len(gammas)])
    accuracies_test_by_deg = np.zeros([len(degrees), len(gammas)])
    
    # For each degree, compute the least squares weights, the predictions and the accuracies
    previous_deg = 1
    for deg_id, deg in enumerate(degrees):
        print('++ Degree', deg, '++')
                
        # Add powers of the chosen columns
        len_data = tx_cross_val_train.shape[1]
        tx_cross_val_train = add_powers(tx_cross_val_train, range(previous_deg+1, deg+1), range(len_kept_data))
        tx_cross_val_test = add_powers(tx_cross_val_test, range(previous_deg+1, deg+1), range(len_kept_data))
        if stdize: 
            tx_cross_val_train[:,len_data:] = standardize(tx_cross_val_train[:,len_data:])[0]
            tx_cross_val_test[:,len_data:] = standardize(tx_cross_val_test[:,len_data:])[0]
                
        for gamma_id, single_gamma in enumerate(gammas):
            print('>> Gamma', single_gamma, '<<')
            
            # Compute the best weights on the training set
            initial_w = np.zeros(tx_cross_val_train.shape[1])
            weights, loss = least_squares_GD(y_cross_val_train, tx_cross_val_train, initial_w, max_iters, \
                                             single_gamma, fct='mse');

            # Compute the predictions
            y_predicted_cross_val_train = predict_labels(weights, tx_cross_val_train)
            y_predicted_cross_val_test = predict_labels(weights, tx_cross_val_test)

            # Compute the accuracies for each degree
            accuracies_train_by_deg[deg_id, gamma_id] = \
                np.sum(y_predicted_cross_val_train == y_cross_val_train)/len(y_cross_val_train)
            accuracies_test_by_deg[deg_id, gamma_id] = \
                np.sum(y_predicted_cross_val_test == y_cross_val_test)/len(y_cross_val_test)

        # Update the previous degree to the actual degree
        previous_deg = deg
        
    return accuracies_train_by_deg, accuracies_test_by_deg

In [23]:
def cross_validation_GD(y_single_jet_train, tx_single_jet_train, degrees, gammas, k_fold, seed, max_iters):
    
    # Get the indices so that we get the k'th subgroup in test, others in train, for each k
    k_indices = build_k_indices(y_single_jet_train, k_fold, seed)
    
    # Initialize matrix of computed accuracies for each degree and each fold
    accuracies_train_by_fold = np.zeros([len(degrees), len(gammas), k_fold])
    accuracies_test_by_fold = np.zeros([len(degrees), len(gammas), k_fold])
    
    # Preprocess training dataset
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'after')
    
    for k in range(k_fold):
        print('--- Fold', k, '---')
        # Create the testing set for this fold number
        k_index = k_indices[k] # Indices of the testing set for fold k
        y_cross_val_test = y_single_jet_train[k_index]
        tx_cross_val_test = tx_single_jet_train_preprocessed[k_index,:]
        
        # Create the training set for this fold number
        mask = np.ones(len(y_single_jet_train), dtype=bool) # set all elements to True
        mask[k_index] = False # set test elements to False
        y_cross_val_train = y_single_jet_train[mask] # select only True elements (ie train elements)
        tx_cross_val_train = tx_single_jet_train_preprocessed[mask,:]
        
        # Compute the accuracies for each degree
        accuracies_train_by_fold[:,:,k], accuracies_test_by_fold[:,:,k] = cross_validation_one_fold_GD\
            (y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, \
                                 degrees, gammas, len_kept_data, max_iters, True)
    
    # Compute the mean accuracies over the folds, for each degree
    mean_accuracies_train_by_deg = np.mean(accuracies_train_by_fold, axis=2)
    mean_accuracies_test_by_deg = np.mean(accuracies_test_by_fold, axis=2)
    
    # Get the index of the best accuracy in the testing set
    max_id_deg_test, max_id_gamma_test = \
        np.unravel_index(mean_accuracies_test_by_deg.argmax(), mean_accuracies_test_by_deg.shape)
    
    # Find the optimal degree and the corresponding accuracies in the training and testing sets
    best_deg = degrees[max_id_deg_test]
    best_gamma = gammas[max_id_gamma_test]
    best_accuracy_test = mean_accuracies_test_by_deg[max_id_deg_test, max_id_gamma_test]
    corresponding_accuracy_train = mean_accuracies_train_by_deg[max_id_deg_test, max_id_gamma_test]
    
    print('Best accuracy test =', best_accuracy_test, 'with degree =', best_deg, 'and gamma =', best_gamma)
    print('Corresponding accuracy train =', corresponding_accuracy_train)
    
    return best_deg, best_gamma, best_accuracy_test, corresponding_accuracy_train

In [24]:
degrees = range(6,11)
gammas = np.logspace(-5,-1,5)
k_fold = 5
seed = 1
max_iters = 300

In [25]:
mask_jets_train = split_jets_mask(tx_train)
mask_jets_test = split_jets_mask(tx_test)
len_mask = len(mask_jets_train)

y_predicted_train = np.zeros(len(y_train))
y_predicted_test = np.zeros(tx_test.shape[0])
best_degrees = np.zeros(len_mask)
best_gammas = np.zeros(len_mask)

In [26]:
for jet_id in range(len_mask):
    print('***** Jet ', jet_id, '*****')
    # SEPARATE THE WHOLE DATA SET TO GET ONLY THE PART THAT HAVE THE RIGHT NUMBER OF JETS
    tx_single_jet_train = tx_train[mask_jets_train[jet_id]]
    tx_single_jet_test = tx_test[mask_jets_test[jet_id]]
    y_single_jet_train = y_train[mask_jets_train[jet_id]]
    
    # CALL CROSS VALIDATION FOR A SINGLE JET ON TRAIN PART, FIND BEST DEG, BEST ACCURACY ON TESTING CROSS VAL
    best_deg, best_gamma, best_accuracy_test, corresponding_accuracy_train = \
        cross_validation_GD(y_single_jet_train, tx_single_jet_train, degrees, gammas, k_fold, seed, max_iters)
    
    # KEEP IN MEMORY THE BEST DEGREE FOR THIS JET
    best_degrees[jet_id] = best_deg
    best_gammas[jet_id] = best_gamma
    
    # PREPROCESS FULL TRAINING AND TESTING DATA
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'after')
    tx_single_jet_test_preprocessed = preprocess_data(tx_single_jet_test, unique_cols, 'after')[0]
    
    # ADD POWERS TO THE CHOSEN COLUMNS
    len_data = tx_single_jet_train_preprocessed.shape[1]
    tx_single_jet_train_preprocessed = add_powers(tx_single_jet_train_preprocessed, range(2,best_deg+1), \
                                                  range(len_kept_data))
    tx_single_jet_test_preprocessed = add_powers(tx_single_jet_test_preprocessed, range(2,best_deg+1), \
                                                 range(len_kept_data))
    tx_single_jet_train_preprocessed[:,len_data:] = standardize(tx_single_jet_train_preprocessed[:,len_data:])[0]
    tx_single_jet_test_preprocessed[:,len_data:] = standardize(tx_single_jet_test_preprocessed[:,len_data:])[0]
    
    # COMPUTE THE BEST WEIGHTS AND FULL ACCURACY ON TRAINING FULL SET - ONE JET
    initial_w = np.zeros(tx_single_jet_train_preprocessed.shape[1])
    weights, loss = least_squares_GD(y_single_jet_train, tx_single_jet_train_preprocessed, initial_w, max_iters, \
                                             best_gamma, fct='mse');
    
    # COMPUTE THE PREDICTIONS ON THE FULL TESTING SET - SINGLE JET
    y_predicted_single_jet_train = predict_labels(weights, tx_single_jet_train_preprocessed)
    y_predicted_single_jet_test = predict_labels(weights, tx_single_jet_test_preprocessed)
    
    # ADD THE PREDICTIONS TO y_predicted_test AND y_predicted_train
    y_predicted_train[mask_jets_train[jet_id]] = y_predicted_single_jet_train
    y_predicted_test[mask_jets_test[jet_id]] = y_predicted_single_jet_test
    
    # COMPUTE THE ACCURACY train ON JET
    accuracy_train_single_jet = np.sum(y_predicted_single_jet_train == y_single_jet_train)/len(y_single_jet_train)
    
    # PRINT ACCURACY train ON JET
    print('Accuracy full train on jet', jet_id, '=', accuracy_train_single_jet)

***** Jet  0 *****
--- Fold 0 ---
++ Degree 6 ++
>> Gamma 1e-05 <<
Gradient Descent(0/299): loss=0.4999999999999999, w0=-4.468678085971062e-07, w1=-2.8951081650510586e-06
Gradient Descent(1/299): loss=0.49998009864094545, w0=-8.935129252750068e-07, w1=-5.7897363107493205e-06
Gradient Descent(2/299): loss=0.4999602032022705, w0=-1.3399354445383042e-06, w1=-8.683884561513866e-06
Gradient Descent(3/299): loss=0.49994031368090047, w0=-1.7861354608539977e-06, w1=-1.1577553041724759e-05
Gradient Descent(4/299): loss=0.49992043007376225, w0=-2.2321130686514964e-06, w1=-1.4470741875723064e-05
Gradient Descent(5/299): loss=0.49990055237778475, w0=-2.677868362322635e-06, w1=-1.7363451187810854e-05
Gradient Descent(6/299): loss=0.4998806805898989, w0=-3.1234014362216873e-06, w1=-2.025568110225123e-05
Gradient Descent(7/299): loss=0.49986081470703747, w0=-3.568712384665381e-06, w1=-2.314743174326833e-05
Gradient Descent(8/299): loss=0.4998409547261352, w0=-4.013801301932913e-06, w1=-2.603870323504

Gradient Descent(133/299): loss=0.4777631061550427, w0=-0.0004330348509917416, w1=-0.0034958890125139637
Gradient Descent(134/299): loss=0.4776218997905834, w0=-0.0004352310869277964, w1=-0.003519379331533181
Gradient Descent(135/299): loss=0.4774810049985013, w0=-0.00043741487111861996, w1=-0.0035428353146701253
Gradient Descent(136/299): loss=0.47734042040639946, w0=-0.00043958625869325074, w1=-0.0035662570443541013
Gradient Descent(137/299): loss=0.47720014464972327, w0=-0.00044174530455723333, w1=-0.003589644602767453
Gradient Descent(138/299): loss=0.4770601763717084, w0=-0.00044389206339348814, w1=-0.0036129980718463935
Gradient Descent(139/299): loss=0.4769205142233307, w0=-0.0004460265896631774, w1=-0.003636317533281831
Gradient Descent(140/299): loss=0.476781156863255, w0=-0.00044814893760656855, w1=-0.0036596030685201956
Gradient Descent(141/299): loss=0.4766421029577852, w0=-0.0004502591612438934, w1=-0.0036828547587642595
Gradient Descent(142/299): loss=0.476503351180814, w

Gradient Descent(202/299): loss=0.19602303633387985, w0=0.012080450258335264, w1=-0.047759994643453665
Gradient Descent(203/299): loss=0.1958584399655177, w0=0.012146984395371568, w1=-0.04778048034918043
Gradient Descent(204/299): loss=0.19569562994252132, w0=0.01221336493463504, w1=-0.047800568836137654
Gradient Descent(205/299): loss=0.1955345771312722, w0=0.012279592589329955, w1=-0.04782026363112197
Gradient Descent(206/299): loss=0.1953752529377108, w0=0.012345668079959984, w1=-0.047839568216281825
Gradient Descent(207/299): loss=0.19521762929670197, w0=0.012411592133919597, w1=-0.0478584860300604
Gradient Descent(208/299): loss=0.19506167866162044, w0=0.012477365485098089, w1=-0.04787702046811211
Gradient Descent(209/299): loss=0.19490737399415275, w0=0.012542988873495893, w1=-0.04789517488419371
Gradient Descent(210/299): loss=0.1947546887543094, w0=0.012608463044852794, w1=-0.047912952591030546
Gradient Descent(211/299): loss=0.1946035968906437, w0=0.01267378875028773, w1=-0.04

Gradient Descent(56/299): loss=0.4895724627209279, w0=-0.00022109186595251765, w1=-0.001576593612049372
Gradient Descent(57/299): loss=0.4894007237453892, w0=-0.00022440873767821847, w1=-0.001602980315958779
Gradient Descent(58/299): loss=0.48922944373669, w0=-0.00022770787946159443, w1=-0.0016293253376602067
Gradient Descent(59/299): loss=0.48905862040816644, w0=-0.00023098936992794737, w1=-0.001655628784127119
Gradient Descent(60/299): loss=0.48888825148743137, w0=-0.0002342532873775746, w1=-0.001681890761993048
Gradient Descent(61/299): loss=0.4887183347162742, w0=-0.00023749970978707022, w1=-0.0017081113775527942
Gradient Descent(62/299): loss=0.4885488678505619, w0=-0.00024072871481062118, w1=-0.0017342907367636252
Gradient Descent(63/299): loss=0.4883798486601411, w0=-0.00024394037978129842, w1=-0.0017604289452464686
Gradient Descent(64/299): loss=0.48821127492874017, w0=-0.0002471347817123427, w1=-0.0017865261082871
Gradient Descent(65/299): loss=0.48804314445387253, w0=-0.00025

Gradient Descent(153/299): loss=2.0596638122967546e+140, w0=1.0836569803569184e+69, w1=8.963701402023777e+68
Gradient Descent(154/299): loss=1.762445636947949e+141, w0=-3.1699435505696777e+69, w1=-2.622086874687867e+69
Gradient Descent(155/299): loss=1.5081172979065384e+142, w0=9.272807074512334e+69, w1=7.67020148268006e+69
Gradient Descent(156/299): loss=1.2904896108929407e+143, w0=-2.7125073260586443e+70, w1=-2.2437086792523044e+70
Gradient Descent(157/299): loss=1.1042665170238104e+144, w0=7.934701902884956e+70, w1=6.563359057411768e+70
Gradient Descent(158/299): loss=9.449162010503466e+144, w0=-2.321081078115585e+71, w1=-1.9199320533387727e+71
Gradient Descent(159/299): loss=8.085608077784059e+145, w0=6.789690951373241e+71, w1=5.616238662541265e+71
Gradient Descent(160/299): loss=6.918820728743479e+146, w0=-1.9861392887053635e+72, w1=-1.6428777601671562e+72
Gradient Descent(161/299): loss=5.920405715436277e+147, w0=5.8099099095831604e+72, w1=4.8057917354077904e+72
Gradient Descent(

...

Gradient Descent(227/299): loss=0.49579428303088025, w0=4.422672112104536e-05, w1=-0.0005607609288013962
Gradient Descent(228/299): loss=0.49577614592903146, w0=4.442074031131361e-05, w1=-0.0005631874969539522
Gradient Descent(229/299): loss=0.49575801217564885, w0=4.4614759459283544e-05, w1=-0.0005656137810985026
Gradient Descent(230/299): loss=0.4957398817697676, w0=4.480877855970705e-05, w1=-0.0005680397812790976
Gradient Descent(231/299): loss=0.49572175471042285, w0=4.50027976073382e-05, w1=-0.0005704654975397797
Gradient Descent(232/299): loss=0.49570363099665055, w0=4.519681659693325e-05, w1=-0.0005728909299245832
Gradient Descent(233/299): loss=0.49568551062748667, w0=4.5390835523250586e-05, w1=-0.0005753160784775351
Gradient Descent(234/299): loss=0.49566739360196754, w0=4.5584854381050794e-05, w1=-0.000577740943242654
Gradient Descent(235/299): loss=0.4956492799191298, w0=4.577887316509662e-05, w1=-0.0005801655242639512
Gradient Descent(236/299): loss=0.49563116957801057, w0=

Gradient Descent(30/299): loss=0.31739398233472677, w0=0.0031455766914769887, w1=-0.026823199309940003
Gradient Descent(31/299): loss=0.3145490434082041, w0=0.0032018481468374872, w1=-0.027130532635130905
Gradient Descent(32/299): loss=0.3117725258976509, w0=0.0032583992183784637, w1=-0.027427889310698964
Gradient Descent(33/299): loss=0.3090617055733796, w0=0.00331532449176617, w1=-0.02771586047422923
Gradient Descent(34/299): loss=0.30641406825847345, w0=0.003372706520364095, w1=-0.027994985536780797
Gradient Descent(35/299): loss=0.303827285332033, w0=0.0034306169768397073, w1=-0.0282657578101649
Gradient Descent(36/299): loss=0.3012991926914246, w0=0.00348911770159444, w1=-0.028528629422191306
Gradient Descent(37/299): loss=0.29882777261926075, w0=0.003548261657099535, w1=-0.028784015621154308
Gradient Descent(38/299): loss=0.29641113810049513, w0=0.0036080937965029965, w1=-0.029032298555061734
Gradient Descent(39/299): loss=0.294047519214662, w0=0.0036686518541694853, w1=-0.029273

Gradient Descent(178/299): loss=0.4966297128180974, w0=3.47968283402917e-05, w1=-0.0004414930355566694
Gradient Descent(179/299): loss=0.49661110251392904, w0=3.499169522606948e-05, w1=-0.00044393338433397765
Gradient Descent(180/299): loss=0.4965924957639578, w0=3.518656687500613e-05, w1=-0.0004463734459346127
Gradient Descent(181/299): loss=0.4965738925671219, w0=3.538144327941375e-05, w1=-0.00044881322040366244
Gradient Descent(182/299): loss=0.4965552929223602, w0=3.557632443160753e-05, w1=-0.0004512527077862065
Gradient Descent(183/299): loss=0.4965366968286114, w0=3.5771210323905705e-05, w1=-0.00045369190812731634
Gradient Descent(184/299): loss=0.4965181042848151, w0=3.59661009486296e-05, w1=-0.0004561308214720552
Gradient Descent(185/299): loss=0.4964995152899108, w0=3.616099629810357e-05, w1=-0.0004585694478654783
Gradient Descent(186/299): loss=0.49648092984283876, w0=3.6355896364655074e-05, w1=-0.00046100778735263257
Gradient Descent(187/299): loss=0.4964623479425394, w0=3.6

Gradient Descent(63/299): loss=0.24948503305140632, w0=0.005326553274875439, w1=-0.03360387637970552
Gradient Descent(64/299): loss=0.24805999159763767, w0=0.005405610306575933, w1=-0.03374193352802368
Gradient Descent(65/299): loss=0.24666216473547659, w0=0.005485309242853694, w1=-0.03387740569933381
Gradient Descent(66/299): loss=0.24529095601876125, w0=0.005565632125200309, w1=-0.03401036146119956
Gradient Descent(67/299): loss=0.24394578475249992, w0=0.005646561172573864, w1=-0.03414086638699613
Gradient Descent(68/299): loss=0.2426260853801053, w0=0.005728078816059133, w1=-0.03426898324350981
Gradient Descent(69/299): loss=0.2413313069110843, w0=0.005810167728574747, w1=-0.03439477216403654
Gradient Descent(70/299): loss=0.24006091238529859, w0=0.005892810850129893, w1=-0.03451829080825958
Gradient Descent(71/299): loss=0.23881437837035902, w0=0.0059759914090872146, w1=-0.03463959451006154
Gradient Descent(72/299): loss=0.23759119448910346, w0=0.006059692939846684, w1=-0.034758736

KeyboardInterrupt: 

In [ ]:
# CREATE CSV SUBMISSION
#create_csv_submission(ids_test, y_predicted_test, 'output/trial.csv')

# COMPUTE ACCURACY ON FULL train
total_accuracy_train = np.sum(y_predicted_train == y_train)/len(y_train)*100
print('Total accuracy train =', total_accuracy_train, 'with degrees =', best_degrees, 'and gammas =', best_gammas)

In [ ]:
total_accuracy_test = np.sum(y_predicted_test == y_test)/len(y_test)*100
print('Total accuracy test =', total_accuracy_test, 'with degrees =', best_degrees)

In [ ]:
np.sum(y_predicted_test==-1)

In [ ]:
np.sum(y_predicted_test==1)

In [ ]:
y_predicted_test[:200]

## Ridge regression   

In [26]:
def cross_validation_one_fold_ridge(y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, \
                                    degrees, lambdas, len_kept_data, stdize=False):
    
    accuracies_train_by_deg = np.zeros([len(degrees), len(lambdas)])
    accuracies_test_by_deg = np.zeros([len(degrees), len(lambdas)])
    
    # For each degree, compute the least squares weights, the predictions and the accuracies
    previous_deg = 1
    for deg_id, deg in enumerate(degrees):
        print('++ Degree', deg, '++')
                
        # Add powers of the chosen columns
        len_data = tx_cross_val_train.shape[1]
        tx_cross_val_train = add_powers(tx_cross_val_train, range(previous_deg+1, deg+1), range(len_kept_data))
        tx_cross_val_test = add_powers(tx_cross_val_test, range(previous_deg+1, deg+1), range(len_kept_data))
        if stdize: 
            tx_cross_val_train[:,len_data:] = standardize(tx_cross_val_train[:,len_data:])[0]
            tx_cross_val_test[:,len_data:] = standardize(tx_cross_val_test[:,len_data:])[0]
                
        for lambda_id, single_lambda in enumerate(lambdas):
            print('>> Lambda', single_lambda, '<<')
            
            # Compute the best weights on the training set
            weights, loss = ridge_regression(y_cross_val_train, tx_cross_val_train, single_lambda, 'mse');

            # Compute the predictions
            y_predicted_cross_val_train = predict_labels(weights, tx_cross_val_train)
            y_predicted_cross_val_test = predict_labels(weights, tx_cross_val_test)

            # Compute the accuracies for each degree
            accuracies_train_by_deg[deg_id, lambda_id] = \
                np.sum(y_predicted_cross_val_train == y_cross_val_train)/len(y_cross_val_train)
            accuracies_test_by_deg[deg_id, lambda_id] = \
                np.sum(y_predicted_cross_val_test == y_cross_val_test)/len(y_cross_val_test)

        # Update the previous degree to the actual degree
        previous_deg = deg
        
    return accuracies_train_by_deg, accuracies_test_by_deg

In [27]:
def cross_validation_ridge(y_single_jet_train, tx_single_jet_train, degrees, lambdas, k_fold, seed):
    
    # Get the indices so that we get the k'th subgroup in test, others in train, for each k
    k_indices = build_k_indices(y_single_jet_train, k_fold, seed)
    
    # Initialize matrix of computed accuracies for each degree and each fold
    accuracies_train_by_fold = np.zeros([len(degrees), len(lambdas), k_fold])
    accuracies_test_by_fold = np.zeros([len(degrees), len(lambdas), k_fold])
    
    # Preprocess training dataset
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'before')
    
    for k in range(k_fold):
        print('--- Fold', k, '---')
        # Create the testing set for this fold number
        k_index = k_indices[k] # Indices of the testing set for fold k
        y_cross_val_test = y_single_jet_train[k_index]
        tx_cross_val_test = tx_single_jet_train_preprocessed[k_index,:]
        
        # Create the training set for this fold number
        mask = np.ones(len(y_single_jet_train), dtype=bool) # set all elements to True
        mask[k_index] = False # set test elements to False
        y_cross_val_train = y_single_jet_train[mask] # select only True elements (ie train elements)
        tx_cross_val_train = tx_single_jet_train_preprocessed[mask,:]
        
        # Compute the accuracies for each degree
        accuracies_train_by_fold[:,:,k], accuracies_test_by_fold[:,:,k] = \
            cross_validation_one_fold_ridge(y_cross_val_train, y_cross_val_test, tx_cross_val_train, \
                                            tx_cross_val_test, degrees, lambdas, len_kept_data, False)
    
    # Compute the mean accuracies over the folds, for each degree
    mean_accuracies_train_by_deg = np.mean(accuracies_train_by_fold, axis=2)
    mean_accuracies_test_by_deg = np.mean(accuracies_test_by_fold, axis=2)
    
    # Get the index of the best accuracy in the testing set
    max_id_deg_test, max_id_lambda_test = \
        np.unravel_index(mean_accuracies_test_by_deg.argmax(), mean_accuracies_test_by_deg.shape)
    
    # Find the optimal degree and the corresponding accuracies in the training and testing sets
    best_deg = degrees[max_id_deg_test]
    best_lambda = lambdas[max_id_lambda_test]
    best_accuracy_test = mean_accuracies_test_by_deg[max_id_deg_test, max_id_lambda_test]
    corresponding_accuracy_train = mean_accuracies_train_by_deg[max_id_deg_test, max_id_lambda_test]
    
    print('Best accuracy test =', best_accuracy_test, 'with degree =', best_deg, 'and lambda =', best_lambda)
    print('Corresponding accuracy train =', corresponding_accuracy_train)
    
    return best_deg, best_lambda, best_accuracy_test, corresponding_accuracy_train

In [28]:
degrees = range(6,11)
lambdas = np.logspace(-9,-2,7)
k_fold = 5
seed = 1

In [29]:
mask_jets_train = split_jets_mask(tx_train)
mask_jets_test = split_jets_mask(tx_test)
len_mask = len(mask_jets_train)

y_predicted_train = np.zeros(len(y_train))
y_predicted_test = np.zeros(tx_test.shape[0])
best_degrees = np.zeros(len_mask)
best_lambdas = np.zeros(len_mask)

In [30]:
for jet_id in range(len_mask):
    print('***** Jet ', jet_id, '*****')
    # SEPARATE THE WHOLE DATA SET TO GET ONLY THE PART THAT HAVE THE RIGHT NUMBER OF JETS
    tx_single_jet_train = tx_train[mask_jets_train[jet_id]]
    tx_single_jet_test = tx_test[mask_jets_test[jet_id]]
    y_single_jet_train = y_train[mask_jets_train[jet_id]]
    
    # CALL CROSS VALIDATION FOR A SINGLE JET ON TRAIN PART, FIND BEST DEG, BEST ACCURACY ON TESTING CROSS VAL
    best_deg, best_lambda, best_accuracy_test, corresponding_accuracy_train = \
        cross_validation_ridge(y_single_jet_train, tx_single_jet_train, degrees, lambdas, k_fold, seed)
    
    # KEEP IN MEMORY THE BEST DEGREE FOR THIS JET
    best_degrees[jet_id] = best_deg
    best_lambdas[jet_id] = best_lambda
    
    # PREPROCESS FULL TRAINING AND TESTING DATA
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'before')
    tx_single_jet_test_preprocessed = preprocess_data(tx_single_jet_test, unique_cols, 'before')[0]
    
    # ADD POWERS TO THE CHOSEN COLUMNS
    len_data = tx_single_jet_train_preprocessed.shape[1]
    tx_single_jet_train_preprocessed = add_powers(tx_single_jet_train_preprocessed, range(2,best_deg+1), \
                                                  range(len_kept_data))
    tx_single_jet_test_preprocessed = add_powers(tx_single_jet_test_preprocessed, range(2,best_deg+1), \
                                                 range(len_kept_data))
    tx_single_jet_train_preprocessed[:,len_data:] = standardize(tx_single_jet_train_preprocessed[:,len_data:])[0]
    tx_single_jet_test_preprocessed[:,len_data:] = standardize(tx_single_jet_test_preprocessed[:,len_data:])[0]
    
    # COMPUTE THE BEST WEIGHTS AND FULL ACCURACY ON TRAINING FULL SET - ONE JET
    initial_w = np.zeros(tx_single_jet_train_preprocessed.shape[1])
    weights, loss = ridge_regression(y_single_jet_train, tx_single_jet_train_preprocessed, \
                                             best_lambda, fct='mse');
    
    # COMPUTE THE PREDICTIONS ON THE FULL TESTING SET - SINGLE JET
    y_predicted_single_jet_train = predict_labels(weights, tx_single_jet_train_preprocessed)
    y_predicted_single_jet_test = predict_labels(weights, tx_single_jet_test_preprocessed)
    
    # ADD THE PREDICTIONS TO y_predicted_test AND y_predicted_train
    y_predicted_train[mask_jets_train[jet_id]] = y_predicted_single_jet_train
    y_predicted_test[mask_jets_test[jet_id]] = y_predicted_single_jet_test
    
    # COMPUTE THE ACCURACY train ON JET
    accuracy_train_single_jet = np.sum(y_predicted_single_jet_train == y_single_jet_train)/len(y_single_jet_train)
    
    # PRINT ACCURACY train ON JET
    print('Accuracy full train on jet', jet_id, '=', accuracy_train_single_jet)

***** Jet  0 *****
--- Fold 0 ---
++ Degree 6 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 7 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 8 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 9 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 10 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 

>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 10 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
--- Fold 3 ---
++ Degree 6 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 7 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 8 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.0

>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 8 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 9 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
++ Degree 10 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.000681292069058 <<
>> Lambda 0.01 <<
--- Fold 1 ---
++ Degree 6 ++
>> Lambda 1e-09 <<
>> Lambda 1.46779926762e-08 <<
>> Lambda 2.15443469003e-07 <<
>> Lambda 3.16227766017e-06 <<
>> Lambda 4.64158883361e-05 <<
>> Lambda 0.0

In [31]:
# CREATE CSV SUBMISSION
#create_csv_submission(ids_test, y_predicted_test, 'output/trial.csv')

# COMPUTE ACCURACY ON FULL train
total_accuracy_train = np.sum(y_predicted_train == y_train)/len(y_train)*100
print('Total accuracy train =', total_accuracy_train, 'with degrees =', best_degrees, 'and lambda =', best_lambdas)

Total accuracy train = 82.1136 with degrees = [ 10.  10.   9.  10.] and lambda = [  4.64158883e-05   1.00000000e-02   6.81292069e-04   1.00000000e-02]


In [32]:
total_accuracy_test = np.sum(y_predicted_test == y_test)/len(y_test)*100
print('Total accuracy test =', total_accuracy_test, 'with degrees =', best_degrees, 'and lambda =', best_lambdas)

Total accuracy test = 79.9717333333 with degrees = [ 10.  10.   9.  10.] and lambda = [  4.64158883e-05   1.00000000e-02   6.81292069e-04   1.00000000e-02]


In [33]:
np.sum(y_predicted_test==-1)

130484

In [34]:
np.sum(y_predicted_test==1)

57016

In [35]:
y_predicted_test[:200]

array([-1., -1., -1., -1., -1., -1.,  1.,  1., -1.,  1., -1., -1.,  1.,
       -1., -1., -1.,  1., -1., -1., -1., -1., -1., -1.,  1., -1., -1.,
       -1.,  1.,  1.,  1., -1., -1.,  1.,  1., -1., -1.,  1.,  1., -1.,
       -1., -1., -1.,  1., -1., -1., -1.,  1., -1.,  1.,  1., -1.,  1.,
       -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,
       -1., -1., -1., -1., -1., -1.,  1., -1.,  1., -1.,  1.,  1., -1.,
        1.,  1., -1., -1., -1.,  1., -1., -1., -1., -1., -1., -1., -1.,
       -1., -1.,  1.,  1., -1., -1., -1., -1., -1., -1., -1., -1.,  1.,
       -1., -1.,  1.,  1., -1., -1.,  1., -1.,  1., -1., -1.,  1., -1.,
       -1., -1.,  1.,  1., -1., -1., -1., -1.,  1., -1., -1.,  1., -1.,
       -1., -1., -1.,  1., -1.,  1., -1., -1., -1., -1., -1., -1.,  1.,
       -1.,  1., -1., -1.,  1.,  1.,  1.,  1., -1., -1., -1., -1., -1.,
       -1., -1.,  1., -1., -1., -1., -1., -1.,  1., -1.,  1.,  1., -1.,
       -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1

##  SGD

In [36]:
def cross_validation_one_fold_SGD(y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, \
                                 degrees, gammas, len_kept_data, max_iters, batch_size, stdize=False):
    
    accuracies_train_by_deg = np.zeros([len(degrees), len(gammas)])
    accuracies_test_by_deg = np.zeros([len(degrees), len(gammas)])
    
    # For each degree, compute the least squares weights, the predictions and the accuracies
    previous_deg = 1
    for deg_id, deg in enumerate(degrees):
        print('++ Degree', deg, '++')
                
        # Add powers of the chosen columns
        len_data = tx_cross_val_train.shape[1]
        tx_cross_val_train = add_powers(tx_cross_val_train, range(previous_deg+1, deg+1), range(len_kept_data))
        tx_cross_val_test = add_powers(tx_cross_val_test, range(previous_deg+1, deg+1), range(len_kept_data))
        if stdize: 
            tx_cross_val_train[:,len_data:] = standardize(tx_cross_val_train[:,len_data:])[0]
            tx_cross_val_test[:,len_data:] = standardize(tx_cross_val_test[:,len_data:])[0]
                
        for gamma_id, single_gamma in enumerate(gammas):
            print('>> Gamma', single_gamma, '<<')
            
            # Compute the best weights on the training set
            initial_w = np.zeros(tx_cross_val_train.shape[1])
            weights, loss = least_squares_SGD(y_cross_val_train, tx_cross_val_train, initial_w, max_iters, \
                                             single_gamma, batch_size);

            # Compute the predictions
            y_predicted_cross_val_train = predict_labels(weights, tx_cross_val_train)
            y_predicted_cross_val_test = predict_labels(weights, tx_cross_val_test)

            # Compute the accuracies for each degree
            accuracies_train_by_deg[deg_id, gamma_id] = \
                np.sum(y_predicted_cross_val_train == y_cross_val_train)/len(y_cross_val_train)
            accuracies_test_by_deg[deg_id, gamma_id] = \
                np.sum(y_predicted_cross_val_test == y_cross_val_test)/len(y_cross_val_test)

        # Update the previous degree to the actual degree
        previous_deg = deg
        
    return accuracies_train_by_deg, accuracies_test_by_deg

In [37]:
def cross_validation_SGD(y_single_jet_train, tx_single_jet_train, degrees, gammas, k_fold, seed, max_iters, \
                        batch_size):
    
    # Get the indices so that we get the k'th subgroup in test, others in train, for each k
    k_indices = build_k_indices(y_single_jet_train, k_fold, seed)
    
    # Initialize matrix of computed accuracies for each degree and each fold
    accuracies_train_by_fold = np.zeros([len(degrees), len(gammas), k_fold])
    accuracies_test_by_fold = np.zeros([len(degrees), len(gammas), k_fold])
    
    # Preprocess training dataset
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'after')
    
    for k in range(k_fold):
        print('--- Fold', k, '---')
        # Create the testing set for this fold number
        k_index = k_indices[k] # Indices of the testing set for fold k
        y_cross_val_test = y_single_jet_train[k_index]
        tx_cross_val_test = tx_single_jet_train_preprocessed[k_index,:]
        
        # Create the training set for this fold number
        mask = np.ones(len(y_single_jet_train), dtype=bool) # set all elements to True
        mask[k_index] = False # set test elements to False
        y_cross_val_train = y_single_jet_train[mask] # select only True elements (ie train elements)
        tx_cross_val_train = tx_single_jet_train_preprocessed[mask,:]
        
        # Compute the accuracies for each degree
        accuracies_train_by_fold[:,:,k], accuracies_test_by_fold[:,:,k] = \
            cross_validation_one_fold_SGD(y_cross_val_train, y_cross_val_test, tx_cross_val_train, \
                                          tx_cross_val_test, degrees, gammas, len_kept_data, max_iters, \
                                          batch_size, True)
    
    # Compute the mean accuracies over the folds, for each degree
    mean_accuracies_train_by_deg = np.mean(accuracies_train_by_fold, axis=2)
    mean_accuracies_test_by_deg = np.mean(accuracies_test_by_fold, axis=2)
    
    # Get the index of the best accuracy in the testing set
    max_id_deg_test, max_id_gamma_test = \
        np.unravel_index(mean_accuracies_test_by_deg.argmax(), mean_accuracies_test_by_deg.shape)
    
    # Find the optimal degree and the corresponding accuracies in the training and testing sets
    best_deg = degrees[max_id_deg_test]
    best_gamma = gammas[max_id_gamma_test]
    best_accuracy_test = mean_accuracies_test_by_deg[max_id_deg_test, max_id_gamma_test]
    corresponding_accuracy_train = mean_accuracies_train_by_deg[max_id_deg_test, max_id_gamma_test]
    
    print('Best accuracy test =', best_accuracy_test, 'with degree =', best_deg, 'and gamma =', best_gamma)
    print('Corresponding accuracy train =', corresponding_accuracy_train)
    
    return best_deg, best_gamma, best_accuracy_test, corresponding_accuracy_train

In [38]:
degrees = range(3,10)
gammas = np.logspace(-6,-1,5)
k_fold = 5
seed = 1
max_iters = 300
batch_size = 1

In [39]:
mask_jets_train = split_jets_mask(tx_train)
mask_jets_test = split_jets_mask(tx_test)
len_mask = len(mask_jets_train)

y_predicted_train = np.zeros(len(y_train))
y_predicted_test = np.zeros(tx_test.shape[0])
best_degrees = np.zeros(len_mask)
best_gammas = np.zeros(len_mask)

In [40]:
for jet_id in range(len_mask):
    print('***** Jet ', jet_id, '*****')
    # SEPARATE THE WHOLE DATA SET TO GET ONLY THE PART THAT HAVE THE RIGHT NUMBER OF JETS
    tx_single_jet_train = tx_train[mask_jets_train[jet_id]]
    tx_single_jet_test = tx_test[mask_jets_test[jet_id]]
    y_single_jet_train = y_train[mask_jets_train[jet_id]]
    
    # CALL CROSS VALIDATION FOR A SINGLE JET ON TRAIN PART, FIND BEST DEG, BEST ACCURACY ON TESTING CROSS VAL
    best_deg, best_gamma, best_accuracy_test, corresponding_accuracy_train = \
        cross_validation_SGD(y_single_jet_train, tx_single_jet_train, degrees, gammas, k_fold, seed, max_iters, \
                            batch_size)
    
    # KEEP IN MEMORY THE BEST DEGREE FOR THIS JET
    best_degrees[jet_id] = best_deg
    best_gammas[jet_id] = best_gamma
    
    # PREPROCESS FULL TRAINING AND TESTING DATA
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'after')
    tx_single_jet_test_preprocessed = preprocess_data(tx_single_jet_test, unique_cols, 'after')[0]
    
    # ADD POWERS TO THE CHOSEN COLUMNS
    len_data = tx_single_jet_train_preprocessed.shape[1]
    tx_single_jet_train_preprocessed = add_powers(tx_single_jet_train_preprocessed, range(2,best_deg+1), \
                                                  range(len_kept_data))
    tx_single_jet_test_preprocessed = add_powers(tx_single_jet_test_preprocessed, range(2,best_deg+1), \
                                                 range(len_kept_data))
    tx_single_jet_train_preprocessed[:,len_data:] = standardize(tx_single_jet_train_preprocessed[:,len_data:])[0]
    tx_single_jet_test_preprocessed[:,len_data:] = standardize(tx_single_jet_test_preprocessed[:,len_data:])[0]
    
    # COMPUTE THE BEST WEIGHTS AND FULL ACCURACY ON TRAINING FULL SET - ONE JET
    initial_w = np.zeros(tx_single_jet_train_preprocessed.shape[1])
    weights, loss = least_squares_SGD(y_single_jet_train, tx_single_jet_train_preprocessed, initial_w, max_iters, \
                                             best_gamma, batch_size);
    
    # COMPUTE THE PREDICTIONS ON THE FULL TESTING SET - SINGLE JET
    y_predicted_single_jet_train = predict_labels(weights, tx_single_jet_train_preprocessed)
    y_predicted_single_jet_test = predict_labels(weights, tx_single_jet_test_preprocessed)
    
    # ADD THE PREDICTIONS TO y_predicted_test AND y_predicted_train
    y_predicted_train[mask_jets_train[jet_id]] = y_predicted_single_jet_train
    y_predicted_test[mask_jets_test[jet_id]] = y_predicted_single_jet_test
    
    # COMPUTE THE ACCURACY train ON JET
    accuracy_train_single_jet = np.sum(y_predicted_single_jet_train == y_single_jet_train)/len(y_single_jet_train)
    
    # PRINT ACCURACY train ON JET
    print('Accuracy full train on jet', jet_id, '=', accuracy_train_single_jet)

***** Jet  0 *****
--- Fold 0 ---
++ Degree 3 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 4 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 5 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 6 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 7 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 8 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 9 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
--- Fol

>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 5 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 6 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 7 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 8 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 9 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
--- Fold 4 ---
++ Degree 3 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 4 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017

>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 5 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 6 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 7 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 8 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 9 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
--- Fold 2 ---
++ Degree 3 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <<
>> Gamma 0.1 <<
++ Degree 4 ++
>> Gamma 1e-06 <<
>> Gamma 1.77827941004e-05 <<
>> Gamma 0.000316227766017 <<
>> Gamma 0.0056234132519 <

In [41]:
# CREATE CSV SUBMISSION
#create_csv_submission(ids_test, y_predicted_test, 'output/trial.csv')

# COMPUTE ACCURACY ON FULL train
total_accuracy_train = np.sum(y_predicted_train == y_train)/len(y_train)*100
print('Total accuracy train =', total_accuracy_train, 'with degrees =', best_degrees, 'and gammas =', best_gammas)

Total accuracy train = 67.7168 with degrees = [ 8.  9.  3.  4.] and gammas = [ 0.00031623  0.00031623  0.00031623  0.00031623]


In [42]:
total_accuracy_test = np.sum(y_predicted_test == y_test)/len(y_test)*100
print('Total accuracy test =', total_accuracy_test, 'with degrees =', best_degrees)

Total accuracy test = 67.8229333333 with degrees = [ 8.  9.  3.  4.]


In [43]:
np.sum(y_predicted_test==-1)

100295

In [44]:
np.sum(y_predicted_test==1)

87205

In [45]:
y_predicted_test[:200]

array([-1., -1., -1.,  1.,  1.,  1., -1.,  1., -1.,  1., -1.,  1.,  1.,
        1., -1.,  1., -1.,  1., -1., -1., -1.,  1., -1., -1., -1.,  1.,
        1.,  1.,  1.,  1., -1.,  1.,  1., -1.,  1.,  1.,  1.,  1., -1.,
       -1.,  1., -1.,  1.,  1.,  1., -1.,  1.,  1.,  1.,  1., -1.,  1.,
       -1., -1., -1.,  1., -1., -1.,  1., -1.,  1., -1., -1.,  1.,  1.,
       -1.,  1., -1.,  1., -1., -1., -1., -1.,  1., -1.,  1., -1., -1.,
        1.,  1., -1., -1.,  1.,  1.,  1., -1., -1.,  1., -1.,  1., -1.,
        1.,  1.,  1.,  1., -1.,  1., -1., -1.,  1., -1., -1., -1.,  1.,
        1.,  1.,  1.,  1., -1., -1., -1.,  1., -1., -1., -1.,  1., -1.,
       -1., -1.,  1.,  1.,  1., -1., -1., -1.,  1.,  1.,  1., -1., -1.,
        1., -1., -1., -1., -1.,  1., -1.,  1., -1.,  1.,  1., -1., -1.,
        1.,  1., -1., -1.,  1., -1.,  1., -1., -1., -1., -1.,  1., -1.,
       -1., -1., -1.,  1., -1., -1., -1., -1., -1., -1.,  1.,  1.,  1.,
        1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,  1., -1

## LOGISTIC REGRESSION

In [46]:
def cross_validation_one_fold_logreg(y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, \
                                    degrees, gammas, len_kept_data, max_iters, stdize=False):
    
    accuracies_train_by_deg = np.zeros([len(degrees), len(gammas)])
    accuracies_test_by_deg = np.zeros([len(degrees), len(gammas)])
    
    # For each degree, compute the least squares weights, the predictions and the accuracies
    previous_deg = 1
    for deg_id, deg in enumerate(degrees):
        print('++ Degree', deg, '++')
                
        # Add powers of the chosen columns
        len_data = tx_cross_val_train.shape[1]
        tx_cross_val_train = add_powers(tx_cross_val_train, range(previous_deg+1, deg+1), range(len_kept_data))
        tx_cross_val_test = add_powers(tx_cross_val_test, range(previous_deg+1, deg+1), range(len_kept_data))
        if stdize: 
            tx_cross_val_train[:,len_data:] = standardize(tx_cross_val_train[:,len_data:])[0]
            tx_cross_val_test[:,len_data:] = standardize(tx_cross_val_test[:,len_data:])[0]
                
        for gamma_id, single_gamma in enumerate(gammas):
            print('>> Gamma', single_gamma, '<<')
            
            # Compute the best weights on the training set
            initial_w = np.zeros(tx_cross_val_train.shape[1])
            weights, loss = logistic_regression(y_cross_val_train, tx_cross_val_train, initial_w, max_iters, \
                                                single_gamma);

            # Compute the predictions
            y_predicted_cross_val_train = predict_labels(weights, tx_cross_val_train)
            y_predicted_cross_val_test = predict_labels(weights, tx_cross_val_test)

            # Compute the accuracies for each degree
            accuracies_train_by_deg[deg_id, gamma_id] = \
                np.sum(y_predicted_cross_val_train == y_cross_val_train)/len(y_cross_val_train)
            accuracies_test_by_deg[deg_id, gamma_id] = \
                np.sum(y_predicted_cross_val_test == y_cross_val_test)/len(y_cross_val_test)

        # Update the previous degree to the actual degree
        previous_deg = deg
        
    return accuracies_train_by_deg, accuracies_test_by_deg

In [47]:
def cross_validation_logreg(y_single_jet_train, tx_single_jet_train, degrees, gammas, k_fold, seed, max_iters):
    
    # Get the indices so that we get the k'th subgroup in test, others in train, for each k
    k_indices = build_k_indices(y_single_jet_train, k_fold, seed)
    
    # Initialize matrix of computed accuracies for each degree and each fold
    accuracies_train_by_fold = np.zeros([len(degrees), len(gammas), k_fold])
    accuracies_test_by_fold = np.zeros([len(degrees), len(gammas), k_fold])
    
    # Preprocess training dataset
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'before')
    
    for k in range(k_fold):
        print('--- Fold', k, '---')
        # Create the testing set for this fold number
        k_index = k_indices[k] # Indices of the testing set for fold k
        y_cross_val_test = y_single_jet_train[k_index]
        tx_cross_val_test = tx_single_jet_train_preprocessed[k_index,:]
        
        # Create the training set for this fold number
        mask = np.ones(len(y_single_jet_train), dtype=bool) # set all elements to True
        mask[k_index] = False # set test elements to False
        y_cross_val_train = y_single_jet_train[mask] # select only True elements (ie train elements)
        tx_cross_val_train = tx_single_jet_train_preprocessed[mask,:]
        
        # Compute the accuracies for each degree
        accuracies_train_by_fold[:,:,k], accuracies_test_by_fold[:,:,k] = \
            cross_validation_one_fold_logreg(y_cross_val_train, y_cross_val_test, tx_cross_val_train, \
                                            tx_cross_val_test, degrees, gammas, len_kept_data, max_iters, False)
    
    # Compute the mean accuracies over the folds, for each degree
    mean_accuracies_train_by_deg = np.mean(accuracies_train_by_fold, axis=2)
    mean_accuracies_test_by_deg = np.mean(accuracies_test_by_fold, axis=2)
    
    # Get the index of the best accuracy in the testing set
    max_id_deg_test, max_id_gamma_test = \
        np.unravel_index(mean_accuracies_test_by_deg.argmax(), mean_accuracies_test_by_deg.shape)
    
    # Find the optimal degree and the corresponding accuracies in the training and testing sets
    best_deg = degrees[max_id_deg_test]
    best_gamma = gammas[max_id_gamma_test]
    best_accuracy_test = mean_accuracies_test_by_deg[max_id_deg_test, max_id_gamma_test]
    corresponding_accuracy_train = mean_accuracies_train_by_deg[max_id_deg_test, max_id_gamma_test]
    
    print('Best accuracy test =', best_accuracy_test, 'with degree =', best_deg, 'and gamma =', best_gamma)
    print('Corresponding accuracy train =', corresponding_accuracy_train)
    
    return best_deg, best_gamma, best_accuracy_test, corresponding_accuracy_train

In [48]:
degrees = range(6,10)
gammas = np.logspace(-9,-2,7)
k_fold = 5
seed = 1
max_iters = 300

In [49]:
mask_jets_train = split_jets_mask(tx_train)
mask_jets_test = split_jets_mask(tx_test)
len_mask = len(mask_jets_train)

y_predicted_train = np.zeros(len(y_train))
y_predicted_test = np.zeros(tx_test.shape[0])
best_degrees = np.zeros(len_mask)
best_lambdas = np.zeros(len_mask)

In [50]:
for jet_id in range(len_mask):
    print('***** Jet ', jet_id, '*****')
    # SEPARATE THE WHOLE DATA SET TO GET ONLY THE PART THAT HAVE THE RIGHT NUMBER OF JETS
    tx_single_jet_train = tx_train[mask_jets_train[jet_id]]
    tx_single_jet_test = tx_test[mask_jets_test[jet_id]]
    y_single_jet_train = y_train[mask_jets_train[jet_id]]
    
    # CALL CROSS VALIDATION FOR A SINGLE JET ON TRAIN PART, FIND BEST DEG, BEST ACCURACY ON TESTING CROSS VAL
    best_deg, best_gamma, best_accuracy_test, corresponding_accuracy_train = \
        cross_validation_logreg(y_single_jet_train, tx_single_jet_train, degrees, gammas, k_fold, seed, max_iters)
    
    # KEEP IN MEMORY THE BEST DEGREE FOR THIS JET
    best_degrees[jet_id] = best_deg
    best_gammas[jet_id] = best_gamma
    
    # PREPROCESS FULL TRAINING AND TESTING DATA
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'before')
    tx_single_jet_test_preprocessed = preprocess_data(tx_single_jet_test, unique_cols, 'before')[0]
    
    # ADD POWERS TO THE CHOSEN COLUMNS
    len_data = tx_single_jet_train_preprocessed.shape[1]
    tx_single_jet_train_preprocessed = add_powers(tx_single_jet_train_preprocessed, range(2,best_deg+1), \
                                                  range(len_kept_data))
    tx_single_jet_test_preprocessed = add_powers(tx_single_jet_test_preprocessed, range(2,best_deg+1), \
                                                 range(len_kept_data))
    tx_single_jet_train_preprocessed[:,len_data:] = standardize(tx_single_jet_train_preprocessed[:,len_data:])[0]
    tx_single_jet_test_preprocessed[:,len_data:] = standardize(tx_single_jet_test_preprocessed[:,len_data:])[0]
    
    # COMPUTE THE BEST WEIGHTS AND FULL ACCURACY ON TRAINING FULL SET - ONE JET
    initial_w = np.zeros(tx_single_jet_train_preprocessed.shape[1])
    weights, loss = logistic_regression(y_single_jet_train, tx_single_jet_train_preprocessed, initial_w,\
                                        max_iters, best_gamma);
    
    # COMPUTE THE PREDICTIONS ON THE FULL TESTING SET - SINGLE JET
    y_predicted_single_jet_train = predict_labels(weights, tx_single_jet_train_preprocessed)
    y_predicted_single_jet_test = predict_labels(weights, tx_single_jet_test_preprocessed)
    
    # ADD THE PREDICTIONS TO y_predicted_test AND y_predicted_train
    y_predicted_train[mask_jets_train[jet_id]] = y_predicted_single_jet_train
    y_predicted_test[mask_jets_test[jet_id]] = y_predicted_single_jet_test
    
    # COMPUTE THE ACCURACY train ON JET
    accuracy_train_single_jet = np.sum(y_predicted_single_jet_train == y_single_jet_train)/len(y_single_jet_train)
    
    # PRINT ACCURACY train ON JET
    print('Accuracy full train on jet', jet_id, '=', accuracy_train_single_jet)

***** Jet  0 *****
--- Fold 0 ---
++ Degree 6 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
++ Degree 7 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
++ Degree 8 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
++ Degree 9 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
--- Fold 1 ---
++ Degree 6 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <

>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
Best accuracy test = 0.644868488912 with degree = 6 and gamma = 2.15443469003e-07
Corresponding accuracy train = 0.643638004383
Accuracy full train on jet 1 = 0.66692450495
***** Jet  2 *****
--- Fold 0 ---
++ Degree 6 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
++ Degree 7 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
++ Degree 8 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
++ Degree 9 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e

>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
++ Degree 8 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
++ Degree 9 ++
>> Gamma 1e-09 <<
>> Gamma 1.46779926762e-08 <<
>> Gamma 2.15443469003e-07 <<
>> Gamma 3.16227766017e-06 <<
>> Gamma 4.64158883361e-05 <<
>> Gamma 0.000681292069058 <<
>> Gamma 0.01 <<
Best accuracy test = 0.710431654676 with degree = 8 and gamma = 1e-09
Corresponding accuracy train = 0.709238031018
Accuracy full train on jet 3 = 0.701672361086


In [51]:
# CREATE CSV SUBMISSION
#create_csv_submission(ids_test, y_predicted_test, 'output/trial.csv')

# COMPUTE ACCURACY ON FULL train
total_accuracy_train = np.sum(y_predicted_train == y_train)/len(y_train)*100
print('Total accuracy train =', total_accuracy_train, 'with degrees =', best_degrees, 'and gamma =', best_gammas)

Total accuracy train = 69.496 with degrees = [ 6.  6.  9.  8.] and gamma = [  1.00000000e-09   2.15443469e-07   1.46779927e-08   1.00000000e-09]


In [52]:
total_accuracy_test = np.sum(y_predicted_test == y_test)/len(y_test)*100
print('Total accuracy test =', total_accuracy_test, 'with degrees =', best_degrees, 'and gamma =', best_gammas)

Total accuracy test = 69.4848 with degrees = [ 6.  6.  9.  8.] and gamma = [  1.00000000e-09   2.15443469e-07   1.46779927e-08   1.00000000e-09]


In [53]:
np.sum(y_predicted_test==-1)

177881

In [54]:
np.sum(y_predicted_test==1)

9619

In [55]:
y_predicted_test[:200]

array([-1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,
       -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,
       -1.,  1., -1.,  1., -1., -1.,  1., -1., -1., -1., -1., -1., -1.,
       -1., -1., -1.,  1., -1., -1., -1., -1., -1., -1., -1., -1.,  1.,
       -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,
       -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,
        1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,
       -1., -1.,  1., -1., -1., -1., -1., -1.,  1., -1., -1., -1., -1.,
       -1., -1., -1., -1., -1., -1., -1.,  1., -1., -1., -1., -1., -1.,
       -1., -1., -1., -1., -1., -1., -1., -1.,  1., -1., -1., -1., -1.,
       -1., -1., -1., -1., -1.,  1., -1., -1., -1., -1., -1., -1., -1.,
       -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,
       -1., -1., -1., -1., -1., -1., -1., -1., -1., -1.,  1., -1., -1.,
       -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1., -1

## LOGISTIC REGULARIZED

In [56]:
def cross_validation_one_fold_logistic_regularized(y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, \
                                 degrees, gammas, lambdas, len_kept_data, max_iters, stdize=False):
    
    accuracies_train_by_deg = np.zeros([len(degrees), len(gammas),len(lambdas)])
    accuracies_test_by_deg = np.zeros([len(degrees), len(gammas),len(lambdas)])
    
    # For each degree, compute the least squares weights, the predictions and the accuracies
    previous_deg = 1
    for deg_id, deg in enumerate(degrees):
        print('++ Degree', deg, '++')
                
        # Add powers of the chosen columns
        len_data = tx_cross_val_train.shape[1]
        tx_cross_val_train = add_powers(tx_cross_val_train, range(previous_deg+1, deg+1), range(len_kept_data))
        tx_cross_val_test = add_powers(tx_cross_val_test, range(previous_deg+1, deg+1), range(len_kept_data))
        if stdize: 
            tx_cross_val_train[:,len_data:] = standardize(tx_cross_val_train[:,len_data:])[0]
            tx_cross_val_test[:,len_data:] = standardize(tx_cross_val_test[:,len_data:])[0]
                
        for gamma_id, single_gamma in enumerate(gammas):
            print('>> Gamma', single_gamma, '<<')
            
            
            for lambda_id, single_lambda in enumerate(lambdas):
                
                print('>> Lambda', single_lambda, '<<')
            # Compute the best weights on the training set
                initial_w = np.zeros(tx_cross_val_train.shape[1])
                weights, loss = reg_logistic_regression(y_cross_val_train, tx_cross_val_train, single_lambda,initial_w, max_iters, \
                                                 single_gamma);

                # Compute the predictions
                y_predicted_cross_val_train = predict_labels(weights, tx_cross_val_train)
                y_predicted_cross_val_test = predict_labels(weights, tx_cross_val_test)

                # Compute the accuracies for each degree
                accuracies_train_by_deg[deg_id, gamma_id,lambda_id] = \
                    np.sum(y_predicted_cross_val_train == y_cross_val_train)/len(y_cross_val_train)
                accuracies_test_by_deg[deg_id, gamma_id,lambda_id] = \
                    np.sum(y_predicted_cross_val_test == y_cross_val_test)/len(y_cross_val_test)

        # Update the previous degree to the actual degree
        previous_deg = deg
        
    return accuracies_train_by_deg, accuracies_test_by_deg

In [57]:
def cross_validation_logistic_regularized(y_single_jet_train, tx_single_jet_train, degrees, gammas, lambdas, k_fold, seed, max_iters):
    
    # Get the indices so that we get the k'th subgroup in test, others in train, for each k
    k_indices = build_k_indices(y_single_jet_train, k_fold, seed)
    
    # Initialize matrix of computed accuracies for each degree and each fold
    accuracies_train_by_fold = np.zeros([len(degrees), len(gammas),len(lambdas), k_fold])
    accuracies_test_by_fold = np.zeros([len(degrees), len(gammas),len(lambdas), k_fold])
    
    # Preprocess training dataset
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'after')
    
    for k in range(k_fold):
        print('--- Fold', k, '---')
        # Create the testing set for this fold number
        k_index = k_indices[k] # Indices of the testing set for fold k
        y_cross_val_test = y_single_jet_train[k_index]
        tx_cross_val_test = tx_single_jet_train_preprocessed[k_index,:]
        
        # Create the training set for this fold number
        mask = np.ones(len(y_single_jet_train), dtype=bool) # set all elements to True
        mask[k_index] = False # set test elements to False
        y_cross_val_train = y_single_jet_train[mask] # select only True elements (ie train elements)
        tx_cross_val_train = tx_single_jet_train_preprocessed[mask,:]
        
        # Compute the accuracies for each degree
        accuracies_train_by_fold[:,:,:,k], accuracies_test_by_fold[:,:,:,k] = cross_validation_one_fold_logistic_regularized\
            (y_cross_val_train, y_cross_val_test, tx_cross_val_train, tx_cross_val_test, \
                                 degrees, gammas, lambdas, len_kept_data, max_iters, True)
    
    # Compute the mean accuracies over the folds, for each degree
    mean_accuracies_train_by_deg = np.mean(accuracies_train_by_fold, axis=3)
    mean_accuracies_test_by_deg = np.mean(accuracies_test_by_fold, axis=3)
    
    # Get the index of the best accuracy in the testing set
    max_id_deg_test, max_id_gamma_test,max_id_lambda = \
        np.unravel_index(mean_accuracies_test_by_deg.argmax(), mean_accuracies_test_by_deg.shape)
    
    # Find the optimal degree and the corresponding accuracies in the training and testing sets
    best_deg = degrees[max_id_deg_test]
    best_gamma = gammas[max_id_gamma_test]
    best_lambda=lambdas[max_id_lambda]
    best_accuracy_test = mean_accuracies_test_by_deg[max_id_deg_test, max_id_gamma_test,max_id_lambda]
    corresponding_accuracy_train = mean_accuracies_train_by_deg[max_id_deg_test, max_id_gamma_test,max_id_lambda]
    
    print('Best accuracy test =', best_accuracy_test, 'with degree =', best_deg)
    print('Corresponding accuracy train =', corresponding_accuracy_train)
    
    return best_deg, best_gamma, best_lambda, best_accuracy_test, corresponding_accuracy_train                        


In [58]:
degrees = range(6,11)
gammas = np.logspace(-8,-2,6)
lambdas = np.logspace(-8,-2,6)

k_fold = 5
seed = 1
max_iters = 300

In [ ]:
mask_jets_train = split_jets_mask(tx_train)
mask_jets_test = split_jets_mask(tx_test)
len_mask = len(mask_jets_train)

y_predicted_train = np.zeros(len(y_train))
y_predicted_test = np.zeros(tx_test.shape[0])
best_degrees = np.zeros(len_mask)
best_gammas = np.zeros(len_mask)
best_lambdas=np.zeros(len_mask)

In [ ]:
for jet_id in range(len_mask):
    print('** Jet ', jet_id, '**')
    # SEPARATE THE WHOLE DATA SET TO GET ONLY THE PART THAT HAVE THE RIGHT NUMBER OF JETS
    tx_single_jet_train = tx_train[mask_jets_train[jet_id]]
    tx_single_jet_test = tx_test[mask_jets_test[jet_id]]
    y_single_jet_train = y_train[mask_jets_train[jet_id]]
    
    # CALL CROSS VALIDATION FOR A SINGLE JET ON TRAIN PART, FIND BEST DEG, BEST ACCURACY ON TESTING CROSS VAL
    best_deg, best_gamma, best_lambda, best_accuracy_test, corresponding_accuracy_train = \
        cross_validation_logistic_regularized(y_single_jet_train, tx_single_jet_train, degrees, gammas, lambdas, k_fold, seed, max_iters)
    
    # KEEP IN MEMORY THE BEST DEGREE FOR THIS JET
    best_degrees[jet_id] = best_deg
    best_gammas[jet_id] = best_gamma
    best_lambdas[jet_id]=best_lambda
    # PREPROCESS FULL TRAINING AND TESTING DATA
    tx_single_jet_train_preprocessed, len_kept_data, unique_cols = \
        preprocess_data(tx_single_jet_train, [], 'after')
    tx_single_jet_test_preprocessed = preprocess_data(tx_single_jet_test, unique_cols, 'after')[0]
    
    # ADD POWERS TO THE CHOSEN COLUMNS
    len_data = tx_single_jet_train_preprocessed.shape[1]
    tx_single_jet_train_preprocessed = add_powers(tx_single_jet_train_preprocessed, range(2,best_deg+1), \
                                                  range(len_kept_data))
    tx_single_jet_test_preprocessed = add_powers(tx_single_jet_test_preprocessed, range(2,best_deg+1), \
                                                 range(len_kept_data))
    tx_single_jet_train_preprocessed[:,len_data:] = standardize(tx_single_jet_train_preprocessed[:,len_data:])[0]
    tx_single_jet_test_preprocessed[:,len_data:] = standardize(tx_single_jet_test_preprocessed[:,len_data:])[0]
    
    # COMPUTE THE BEST WEIGHTS AND FULL ACCURACY ON TRAINING FULL SET - ONE JET
    initial_w = np.zeros(tx_single_jet_train_preprocessed.shape[1])
    weights, loss = reg_logistic_regression(y_single_jet_train, tx_single_jet_train_preprocessed , best_lambda, initial_w, max_iters, best_gamma)
    
    # COMPUTE THE PREDICTIONS ON THE FULL TESTING SET - SINGLE JET
    y_predicted_single_jet_train = predict_labels(weights, tx_single_jet_train_preprocessed)
    y_predicted_single_jet_test = predict_labels(weights, tx_single_jet_test_preprocessed)
    
    # ADD THE PREDICTIONS TO y_predicted_test AND y_predicted_train
    y_predicted_train[mask_jets_train[jet_id]] = y_predicted_single_jet_train
    y_predicted_test[mask_jets_test[jet_id]] = y_predicted_single_jet_test
    
    # COMPUTE THE ACCURACY train ON JET
    accuracy_train_single_jet = np.sum(y_predicted_single_jet_train == y_single_jet_train)/len(y_single_jet_train)
    
    # PRINT ACCURACY train ON JET
    print('Accuracy full train on jet', jet_id, '=', accuracy_train_single_jet)

** Jet  0 **
--- Fold 0 ---
++ Degree 6 ++
>> Gamma 1e-08 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 1.58489319246e-07 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 2.51188643151e-06 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 3.98107170553e-05 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.00063095734448 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.01 <<
>> 

>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 2.51188643151e-06 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 3.98107170553e-05 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.00063095734448 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.01 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
++ Degree 9 ++
>> Gamma 1e-08 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<

>> Lambda 0.01 <<
>> Gamma 3.98107170553e-05 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.00063095734448 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.01 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
--- Fold 3 ---
++ Degree 6 ++
>> Gamma 1e-08 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 1.58489319246e-07 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 2.51188643151e-06 <

>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.01 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
++ Degree 8 ++
>> Gamma 1e-08 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 1.58489319246e-07 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 2.51188643151e-06 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 3.98107170553e-05 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <

>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
++ Degree 10 ++
>> Gamma 1e-08 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 1.58489319246e-07 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 2.51188643151e-06 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 3.98107170553e-05 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.00063095734448 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.5118

>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 1.58489319246e-07 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 2.51188643151e-06 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 3.98107170553e-05 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.00063095734448 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.01 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
++ Degree 8 ++
>

>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 3.98107170553e-05 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.00063095734448 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.01 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
++ Degree 10 ++
>> Gamma 1e-08 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 1.58489319246e-07 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <

>> Lambda 0.01 <<
>> Gamma 3.98107170553e-05 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.00063095734448 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<
>> Lambda 2.51188643151e-06 <<
>> Lambda 3.98107170553e-05 <<
>> Lambda 0.00063095734448 <<
>> Lambda 0.01 <<
>> Gamma 0.01 <<
>> Lambda 1e-08 <<
>> Lambda 1.58489319246e-07 <<


In [ ]:
# CREATE CSV SUBMISSION
#create_csv_submission(ids_test, y_predicted_test, 'output/trial.csv')

# COMPUTE ACCURACY ON FULL train
total_accuracy_train = np.sum(y_predicted_train == y_train)/len(y_train)*100
print('Total accuracy train =', total_accuracy_train, 'with degrees =', best_degrees, \
      ', gammas =', best_gammas, 'and lambdas =', best_lambdas)

In [ ]:
total_accuracy_test = np.sum(y_predicted_test == y_test)/len(y_test)*100
print('Total accuracy test =', total_accuracy_test, 'with degrees =', best_degrees)

In [ ]:
np.sum(y_predicted_test==-1)

In [ ]:
np.sum(y_predicted_test==1)

In [ ]:
y_predicted_test[:200]